In [53]:
# Import dependencies
import cv2
import torch
# import matplotlib.pyplot as plt
import plotly.express as px
import numpy as np
import os
import matplotlib.pyplot as plt

os.environ["KMP_DUPLICATE_LIB_OK"] = "TRUE"

model_type = "DPT_BEiT_L_512"
filepath = "./data/000011.jpg"

In [54]:
# Download the MiDaS
midas = torch.hub.load("intel-isl/MiDaS", model_type)
if torch.cuda.is_available():
    device = torch.device("cuda")
else:
    device = torch.device("cpu")
    print("No GPU found, using CPU instead")
midas.to(device)
midas.eval();

Using cache found in C:\Users\wg19671/.cache\torch\hub\intel-isl_MiDaS_master


In [55]:
def get_depth_estimate(filepath, model_type):

    # Input transformation pipeline
    midas_transforms = torch.hub.load("intel-isl/MiDaS", "transforms")

    if "DPT" in model_type:
        transform = midas_transforms.dpt_transform
    else:
        transform = midas_transforms.small_transform

    # Transform input for midas
    image = cv2.imread(filepath)
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
    input_batch1 = transform(image).to(device)

    # Make a prediction 1
    with torch.no_grad():
        prediction1 = midas(input_batch1)
        prediction1 = torch.nn.functional.interpolate(
            prediction1.unsqueeze(1),
            size=image.shape[:2],
            mode="bicubic",
            align_corners=False,
        ).squeeze()

        output = prediction1.cpu().numpy()

    return output

output = get_depth_estimate(filepath, model_type)

Using cache found in C:\Users\wg19671/.cache\torch\hub\intel-isl_MiDaS_master


In [56]:
# output = (1/output)
# output = output*10
output

array([[ 2424.4219,  2414.132 ,  2419.6665, ...,  2362.5562,  2092.3096,
         1526.2181],
       [ 2415.466 ,  2414.5857,  2422.8494, ...,  2271.616 ,  2216.9116,
         2041.8567],
       [ 2406.9475,  2416.528 ,  2422.849 , ...,  2257.9358,  2296.0098,
         2335.953 ],
       ...,
       [12532.003 , 12548.339 , 12535.585 , ..., 12463.589 , 12477.726 ,
        12577.6045],
       [12460.049 , 12554.178 , 12583.593 , ..., 12500.081 , 12530.887 ,
        12542.527 ],
       [12089.8   , 12485.911 , 12646.379 , ..., 12520.116 , 12505.386 ,
        12483.269 ]], dtype=float32)

In [57]:
fig = px.imshow(output, color_continuous_scale="gray")
fig.update_layout(coloraxis_showscale=False)
fig.update_xaxes(showticklabels=False)
fig.update_yaxes(showticklabels=False)
fig.show()

In [63]:
# Transform input for midas
filepath = "./data/000011.jpg"
filepath = "./data/bible.jpg"
image = cv2.imread(filepath)
image = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
image = cv2.cvtColor(image, cv2.COLOR_GRAY2RGB)


fig = px.imshow(image, color_continuous_scale="gray")
fig.update_layout(coloraxis_showscale=False)
fig.update_xaxes(showticklabels=False)
fig.update_yaxes(showticklabels=False)
fig.show()

